# IMPORT LIBRARIES

In [1]:
import pandas as pd
from sklearn.linear_model import LogisticRegression

import numpy as np
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA

from sklearn.dummy import DummyClassifier
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler

from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC
import xgboost as xgb
from sklearn import metrics
from sklearn.metrics import f1_score, precision_score, recall_score, roc_auc_score, accuracy_score

from sklearn.model_selection import GroupKFold
from collections import Counter
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import precision_score, make_scorer

from sklearn.manifold import TSNE
import matplotlib.pyplot as plt

# SET AND RESET ROWS AND COLS

In [87]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [98]:
pd.reset_option('display.max_columns')
pd.reset_option('display.max_rows')

# READ CSV FILE

In [97]:
df_eye = pd.read_csv('Eye_data.csv')
df_comprehension = pd.read_csv('comprehension_data.csv')
df_fixation = pd.read_csv('fixation_all_paragraph.csv')
df_question = pd.read_csv('Question_data.csv')
df_overall = pd.read_csv('Overall_data_m.csv')
df_eye

Participant  Paragraph  Gazes  AOIGazes  \
0      593890eac6aa16000101f037          1    699       138   
1      593890eac6aa16000101f037          2    727        98   
2      593890eac6aa16000101f037          3    947       248   
3      593890eac6aa16000101f037          4    799       171   
4      593890eac6aa16000101f037          5    163        12   
5      593890eac6aa16000101f037          6    452       176   
6      593890eac6aa16000101f037          7    449        91   
7      593890eac6aa16000101f037          8    188        57   
8      593890eac6aa16000101f037          9    701       297   
9      593890eac6aa16000101f037         10    145        39   
10     593890eac6aa16000101f037         11    738       280   
11     593890eac6aa16000101f037         12    526       175   
12     593890eac6aa16000101f037         13    767       537   
13     593890eac6aa16000101f037         14    288       109   
14     593890eac6aa16000101f037         15    284        76   
15     593890eac6aa16000101f037         16    103        30   
16     593890eac6aa16000101f037         17     94        20   
17     593890eac6aa16000101f037         18    213        83   
18     593890eac6aa16000101f037         19    261        18   
19     593890eac6aa16000101f037         20    775       353   
20     593890eac6aa16000101f037         21    588       269   
21     593890eac6aa16000101f037         22    472       206   
22     593890eac6aa16000101f037         23     64        23   
23     593890eac6aa16000101f037         24    510       156   
24     593890eac6aa16000101f037         25    652       298   
25     593890eac6aa16000101f037         26    752       362   
26     593890eac6aa16000101f037         27    173        27   
27     593890eac6aa16000101f037         28    664       225   
28     593890eac6aa16000101f037         29    569       190   
29     593890eac6aa16000101f037         30    542       311   
30     593890eac6aa16000101f037         31    388       134   
31     593890eac6aa16000101f037         32    398       102   
32     593890eac6aa16000101f037         33    195        22   
33     593890eac6aa16000101f037         34    623       194   
34     593890eac6aa16000101f037         35    316       134   
35     593890eac6aa16000101f037         36    386       154   
36     593890eac6aa16000101f037         37    686       308   
37     593890eac6aa16000101f037         38   1049       624   
38     593890eac6aa16000101f037         39     94        44   
39     593890eac6aa16000101f037         40    514       237   
40     596e1af7a09655000197d4bb          1    416        45   
41     596e1af7a09655000197d4bb          2    527        16   
42     596e1af7a09655000197d4bb          3    455        27   
43     596e1af7a09655000197d4bb          4    567       126   
44     596e1af7a09655000197d4bb          5    157         0   
45     596e1af7a09655000197d4bb          6    228        18   
46     596e1af7a09655000197d4bb          7    260        25   
47     596e1af7a09655000197d4bb          8     49         6   
48     596e1af7a09655000197d4bb          9    273        66   
49     596e1af7a09655000197d4bb         10    114         0   
50     596e1af7a09655000197d4bb         11    234        22   
51     596e1af7a09655000197d4bb         12    208         0   
52     596e1af7a09655000197d4bb         13    388        85   
53     596e1af7a09655000197d4bb         14    252        21   
54     596e1af7a09655000197d4bb         15    267        23   
55     596e1af7a09655000197d4bb         16     88         0   
56     596e1af7a09655000197d4bb         17     60         0   
57     596e1af7a09655000197d4bb         18    105         0   
58     596e1af7a09655000197d4bb         19    114         5   
59     596e1af7a09655000197d4bb         20    420        44   
60     596e1af7a09655000197d4bb         21    274        38   
61     596e1af7a09655000197d4bb         22    274        18   
62     596e1af7a09655000197d4bb         23     26  

# ANALYSIS

In fixation data, there are 397 null values in cluster_sd_duration and 1373 null values in skew_duration column. there are no null values in eye and comprehension data.
After merging eye, fixation and comprehension data, there are null values in cluster_sd_duration (87) and skew_duration (298).

In [110]:
# Count number of participants and instances before mapping and merging all the data
dataframes = [
    ("df_eye_data", df_eye),
    ("df_question_data", df_question),
    ("df_fixation_data", df_fixation)
]
def calculate_statistics(df):
    num_participants = df['Participant'].nunique()
    num_instances = len(df)
    return num_participants, num_instances

for i, (name, df) in enumerate(dataframes, start=1):
    num_participants, num_instances = calculate_statistics(df)
    print(f"{name}:")
    print(f"  Number of participants = {num_participants}")
    print(f"  Number of instances = {num_instances}")


df_eye_data:
  Number of participants = 354
  Number of instances = 14160
df_question_data:
  Number of participants = 354
  Number of instances = 3540
df_fixation_data:
  Number of participants = 338
  Number of instances = 13483


In [99]:
df_question = df_question.rename(columns={'Number': 'Question', 'RT': 'Question_RT'})
df_question

Participant  Question  Question_RT  Correct
0     593890eac6aa16000101f037         1       4.9896        1
1     593890eac6aa16000101f037         2       5.8257        1
2     593890eac6aa16000101f037         3       8.4852        0
3     593890eac6aa16000101f037         4      10.0168        1
4     593890eac6aa16000101f037         5      18.9601        1
...                        ...       ...          ...      ...
3535  63e53dc0bb780ac38cdcf77e         6      12.2569        1
3536  63e53dc0bb780ac38cdcf77e         7      14.1803        1
3537  63e53dc0bb780ac38cdcf77e         8       5.9074        1
3538  63e53dc0bb780ac38cdcf77e         9       7.4726        1
3539  63e53dc0bb780ac38cdcf77e        10       5.4244        1

[3540 rows x 4 columns]

In [24]:
# # Check for null values 
# df_fixation.isnull().sum()

Participant                 0
Paragraph                   0
cluster_num_clusters        0
cluster_avg_duration        0
cluster_sd_duration       397
cluster_skew_duration    1373
dispersion                  0
dtype: int64

## Mapping Questions to Paragraphs

In [100]:
# Mapping of Questions to Paragraphs
mapping = {
    1: [1],
    2: [2],
    3: [13],
    4: [35, 36],
    5: [37, 38, 39],
    6: [34, 35],
    7: [37, 38, 39],
    8: [4],
    9: [2, 3],
    10: [4, 6, 13, 30]
}

expanded_mapping = []
for question, paragraphs in mapping.items():
    for paragraph in paragraphs:
        expanded_mapping.append({'Question': question, 'Paragraph': paragraph})

df_mapping = pd.DataFrame(expanded_mapping)
df_mapping

Question  Paragraph
0          1          1
1          2          2
2          3         13
3          4         35
4          4         36
5          5         37
6          5         38
7          5         39
8          6         34
9          6         35
10         7         37
11         7         38
12         7         39
13         8          4
14         9          2
15         9          3
16        10          4
17        10          6
18        10         13
19        10         30

In [101]:
question_mapping = pd.merge(df_question, df_mapping, on='Question')
question_mapping

Participant  Question  Question_RT  Correct  Paragraph
0     593890eac6aa16000101f037         1       4.9896        1          1
1     596e1af7a09655000197d4bb         1       6.5785        1          1
2     5af835d8e19f8c00019e6dc0         1      12.6838        1          1
3     5b07b71c68eff50001d1c859         1       3.5650        1          1
4     5bd7971b0aac450001f951aa         1      11.2007        1          1
...                        ...       ...          ...      ...        ...
7075  63d3fa78d12b38b131ef6b76        10       7.6856        1         30
7076  63e53dc0bb780ac38cdcf77e        10       5.4244        1          4
7077  63e53dc0bb780ac38cdcf77e        10       5.4244        1          6
7078  63e53dc0bb780ac38cdcf77e        10       5.4244        1         13
7079  63e53dc0bb780ac38cdcf77e        10       5.4244        1         30

[7080 rows x 5 columns]

In [102]:
gaze_question_mapping = pd.merge(question_mapping, df_eye, on=['Participant', 'Paragraph'])
gaze_question_mapping

Participant  Question  Question_RT  Correct  Paragraph  \
0     593890eac6aa16000101f037         1       4.9896        1          1   
1     596e1af7a09655000197d4bb         1       6.5785        1          1   
2     5af835d8e19f8c00019e6dc0         1      12.6838        1          1   
3     5b07b71c68eff50001d1c859         1       3.5650        1          1   
4     5bd7971b0aac450001f951aa         1      11.2007        1          1   
...                        ...       ...          ...      ...        ...   
7075  63d17cf704d2d7053d56b962        10       8.7585        1         30   
7076  63d3fa78d12b38b131ef6b76        10       7.6856        1          6   
7077  63d3fa78d12b38b131ef6b76        10       7.6856        1         30   
7078  63e53dc0bb780ac38cdcf77e        10       5.4244        1          6   
7079  63e53dc0bb780ac38cdcf77e        10       5.4244        1         30   

      Gazes  AOIGazes  OffScreenGazesPix  OffScreenGazesProp  
0       699       138                181                 301  
1       416        45                156                 212  
2       830       136                136                 253  
3       262        93                 47                  53  
4       621       187                 32                  74  
...     ...       ...                ...                 ...  
7075    772       533                  4                  33  
7076    794       274                 99                 130  
7077    664       201                 65                  99  
7078   1331       961                  0                   0  
7079   2340      1701                  2                  14  

[7080 rows x 9 columns]

In [103]:
gaze_fix_que_merge = pd.merge(gaze_question_mapping, df_fixation, on=['Participant', 'Paragraph'])
gaze_fix_que_merge

Participant  Question  Question_RT  Correct  Paragraph  \
0     593890eac6aa16000101f037         1       4.9896        1          1   
1     596e1af7a09655000197d4bb         1       6.5785        1          1   
2     5af835d8e19f8c00019e6dc0         1      12.6838        1          1   
3     5b07b71c68eff50001d1c859         1       3.5650        1          1   
4     5bd7971b0aac450001f951aa         1      11.2007        1          1   
...                        ...       ...          ...      ...        ...   
6741  63d17cf704d2d7053d56b962        10       8.7585        1         30   
6742  63d3fa78d12b38b131ef6b76        10       7.6856        1          6   
6743  63d3fa78d12b38b131ef6b76        10       7.6856        1         30   
6744  63e53dc0bb780ac38cdcf77e        10       5.4244        1          6   
6745  63e53dc0bb780ac38cdcf77e        10       5.4244        1         30   

      Gazes  AOIGazes  OffScreenGazesPix  OffScreenGazesProp  \
0       699       138                181                 301   
1       416        45                156                 212   
2       830       136                136                 253   
3       262        93                 47                  53   
4       621       187                 32                  74   
...     ...       ...                ...                 ...   
6741    772       533                  4                  33   
6742    794       274                 99                 130   
6743    664       201                 65                  99   
6744   1331       961                  0                   0   
6745   2340      1701                  2                  14   

      cluster_num_clusters  cluster_avg_duration  cluster_sd_duration  \
0                        6              0.048183             0.013313   
1                       51              0.050455             0.009926   
2                      138              0.033606             0.020581   
3                       14              0.080571             0.035667   
4                       38              0.080797             0.015477   
...                    ...                   ...                  ...   
6741                    58              0.080571             0.032136   
6742                   218              0.030396             0.003170   
6743                   177              0.031052             0.005820   
6744                   165              0.021177             0.013164   
6745                   307              0.021996             0.014013   

      cluster_skew_duration  dispersion  
0                 -2.332043    0.537245  
1                  1.132722    0.508165  
2                  0.864703    0.453232  
3                  2.975477    0.355419  
4                 -3.901375    0.471612  
...                     ...         ...  
6741               0.319404    0.465988  
6742               1.285993    0.395356  
6743               2.873504    0.361958  
6744               2.234888    0.320407  
6745               2.073853    0.348142  

[6746 rows x 14 columns]

## Standardize

In [105]:
# Standardize columns
columns_to_exclude = ['Participant', 'Question', 'Correct', 'Paragraph']
df_to_standardize = gaze_fix_que_merge.drop(columns=columns_to_exclude)

scaler = StandardScaler()
scaled_features = scaler.fit_transform(df_to_standardize)

df_standardized = pd.DataFrame(scaled_features, columns=df_to_standardize.columns)
gaze_fix_que_z = pd.concat([gaze_fix_que_merge[columns_to_exclude].reset_index(drop=True), df_standardized], axis=1)

gaze_fix_que_z

Participant  Question  Correct  Paragraph  Question_RT  \
0     593890eac6aa16000101f037         1        1          1    -0.708886   
1     596e1af7a09655000197d4bb         1        1          1    -0.544851   
2     5af835d8e19f8c00019e6dc0         1        1          1     0.085448   
3     5b07b71c68eff50001d1c859         1        1          1    -0.855959   
4     5bd7971b0aac450001f951aa         1        1          1    -0.067665   
...                        ...       ...      ...        ...          ...   
6741  63d17cf704d2d7053d56b962        10        1         30    -0.319792   
6742  63d3fa78d12b38b131ef6b76        10        1          6    -0.430556   
6743  63d3fa78d12b38b131ef6b76        10        1         30    -0.430556   
6744  63e53dc0bb780ac38cdcf77e        10        1          6    -0.663998   
6745  63e53dc0bb780ac38cdcf77e        10        1         30    -0.663998   

         Gazes  AOIGazes  OffScreenGazesPix  OffScreenGazesProp  \
0    -0.119902 -0.504823           0.137953            0.404284   
1    -0.554031 -0.753242           0.037180            0.079620   
2     0.081056 -0.510166          -0.043439            0.229185   
3    -0.790271 -0.625026          -0.402191           -0.500398   
4    -0.239556 -0.373936          -0.462655           -0.423792   
...        ...       ...                ...                 ...   
6741 -0.007918  0.550288          -0.575521           -0.573356   
6742  0.025831 -0.141545          -0.192583           -0.219508   
6743 -0.173593 -0.336540          -0.329634           -0.332594   
6744  0.849603  1.693547          -0.591645           -0.693737   
6745  2.397435  3.670210          -0.583583           -0.642666   

      cluster_num_clusters  cluster_avg_duration  cluster_sd_duration  \
0                -0.534860             -0.071420            -0.105832   
1                -0.181841             -0.068585            -0.122042   
2                 0.500662             -0.089613            -0.071052   
3                -0.472101             -0.030999             0.001147   
4                -0.283825             -0.030717            -0.095477   
...                    ...                   ...                  ...   
6741             -0.126927             -0.031000            -0.015750   
6742              1.128251             -0.093619            -0.154377   
6743              0.806612             -0.092801            -0.141693   
6744              0.712473             -0.105125            -0.106548   
6745              1.826444             -0.104102            -0.102481   

      cluster_skew_duration  dispersion  
0                 -1.350325    0.351437  
1                  0.339559    0.196440  
2                  0.208836   -0.096366  
3                  1.238332   -0.617727  
4                 -2.115741    0.001606  
...                     ...         ...  
6741              -0.057124   -0.028372  
6742               0.414314   -0.404858  
6743               1.188597   -0.582875  
6744               0.877122   -0.804346  
6745               0.798580   -0.656519  

[6746 rows x 14 columns]

In [106]:
# gaze_fix_que_z.to_csv('gaze_fix_que_z.csv', index=False)

In [107]:
# Check for null values and remove
gaze_fix_que_z.isnull().sum()

gaze_fix_que_no_null_z = gaze_fix_que_z.dropna()
gaze_fix_que_no_null_z.isnull().sum()


Participant              0
Question                 0
Correct                  0
Paragraph                0
Question_RT              0
Gazes                    0
AOIGazes                 0
OffScreenGazesPix        0
OffScreenGazesProp       0
cluster_num_clusters     0
cluster_avg_duration     0
cluster_sd_duration      0
cluster_skew_duration    0
dispersion               0
dtype: int64

In [108]:
# gaze_fix_que_no_null_z.to_csv('gaze_fix_que_no_null_z.csv', index=False)

In [109]:
# Count number of participants and instances after merging
num_participants = gaze_fix_que_z['Participant'].nunique()
print ("Number of participants in merged data = ", num_participants)

num_instances = len(gaze_fix_que_z)
print ("Number of instances in merged data = ", num_instances)

Number of participants in merged data =  338
Number of instances in merged data =  6746
